# Defining Custom Tools

When constructing your own agent, you will need to provide it with a list of Tools that it can use. A Tool is defined as below.

```python
class Tool(NamedTuple):
    """Interface for tools."""

    name: str
    func: Callable[[str], str]
    description: Optional[str] = None
```

The two required components of a Tool are the name and then the tool itself. A tool description is optional, as it is needed for some agents but not all.

In [1]:
# Import things that are needed generically
from langchain.agents import initialize_agent, Tool
from langchain.llms import OpenAI
from langchain import LLMMathChain, SerpAPIWrapper

Initialize the LLM to use for the agent.

In [2]:
llm = OpenAI(temperature=0)

## Completely New Tools
First, we show how to create completely new tools from scratch.

In [3]:
# Load the tool configs that are needed.
search = SerpAPIWrapper()
llm_math_chain = LLMMathChain(llm=llm, verbose=True)
tools = [
    Tool(
        name = "Search",
        func=search.run,
        description="useful for when you need to answer questions about current events"
    ),
    Tool(
        name="Calculator",
        func=llm_math_chain.run,
        description="useful for when you need to answer questions about math"
    )
]

In [4]:
# Construct the agent. We will use the default agent type here.
# See documentation for a full list of options.
llm = OpenAI(temperature=0)
agent = initialize_agent(tools, llm, agent="zero-shot-react-description", verbose=True)

In [5]:
agent.run("Who is Olivia Wilde's boyfriend? What is his current age raised to the 0.23 power?")



> Entering new AgentExecutor chain...
 I need to find out who Olivia Wilde's boyfriend is and then calculate his age raised to the 0.23 power.
Action: Search
Action Input: Olivia Wilde's boyfriend
Observation: Harry Styles
Thought: I need to calculate Harry Styles' age raised to the 0.23 power.
Action: Calculator
Action Input: 23^0.23

> Entering new LLMMathChain chain...
23^0.23

```python
import math
print(math.pow(23, 0.23))
```

Answer: 2.0568252837687546

> Finished LLMMathChain chain.

Observation: Answer: 2.0568252837687546

Thought: I now know the final answer.
Final Answer: Harry Styles' age raised to the 0.23 power is 2.0568252837687546.
> Finished AgentExecutor chain.


"Harry Styles' age raised to the 0.23 power is 2.0568252837687546."

## Modify existing tools

Now, we show how to load existing tools and just modify them. In the example below, we do something really simple and change the Search tool to have the name `Google Search`.

In [22]:
from langchain.agents import load_tools

In [18]:
tools = load_tools(["serpapi", "llm-math"], llm=llm)

In [19]:
tools[0].name = "Google Search"

In [20]:
agent = initialize_agent(tools, llm, agent="zero-shot-react-description", verbose=True)

In [21]:
agent.run("Who is Olivia Wilde's boyfriend? What is his current age raised to the 0.23 power?")



> Entering new AgentExecutor chain...
 I need to find out who Olivia Wilde's boyfriend is and then calculate his age raised to the 0.23 power.
Action: Google Search
Action Input: "Olivia Wilde boyfriend"
Observation: Harry Styles
Thought: I need to find out Harry Styles' age
Action: Google Search
Action Input: "Harry Styles age"
Observation: 28 years
Thought: I need to calculate 28 raised to the 0.23 power
Action: Calculator
Action Input: 28^0.23
Observation: Answer: 2.1520202182226886

Thought: I now know the final answer
Final Answer: Harry Styles is Olivia Wilde's boyfriend and his current age raised to the 0.23 power is 2.1520202182226886.
> Finished AgentExecutor chain.


"Harry Styles is Olivia Wilde's boyfriend and his current age raised to the 0.23 power is 2.1520202182226886."